# Caravan Club CLs POI Generator 2021


In [1]:
# Install any missing libraries
!pip install simplekml
!pip install pandas
!pip install folium

In [2]:
# imports
import pandas as pd
import simplekml
import folium

In [7]:
df = pd.read_csv("data/cclubclsgarminnavman.csv", names=['Longitude','Latitude','Address'], header=0, sep=',')
print(df.head(5))
print(df['Address'].head())

   Longitude   Latitude                                            Address
0  -4.252842  51.564412  "Eastmoor CL>01792 390708, Kimley Moor Farm, R...
1  -4.276866  51.566973  "Mewslade View>01792 390560, Middleton, Rhossi...
2  -3.039743  52.949784  "Halton Farm>01691 772401, Chirk, Wrexham, Wre...
3  -3.283912  51.474474  "Greendown>07711 576884, Drope Road, St. Georg...
4  -3.262260  51.440710  "Vishwell Farm>02920 593365, Wenvoe, Cardiff, ...
0    "Eastmoor CL>01792 390708, Kimley Moor Farm, R...
1    "Mewslade View>01792 390560, Middleton, Rhossi...
2    "Halton Farm>01691 772401, Chirk, Wrexham, Wre...
3    "Greendown>07711 576884, Drope Road, St. Georg...
4    "Vishwell Farm>02920 593365, Wenvoe, Cardiff, ...
Name: Address, dtype: object


### Extract Site Name, Telephone Number, and Address in to their own columns

In [8]:
df['SiteName'] = df['Address'].str.extract('([a-zA-Z].*(?=>))')
df['PhoneNumber'] = df['Address'].str.extract('([0-9 ]+(?=,))')
# temp data frame with split value columns 
temp = df["Address"].str.split(",", n = 1, expand = True) 

# making separate site address column from new data frame 
df["SiteAddress"]= temp[1]
    
# Dropping old Address columns 
df.drop(columns =["Address"], inplace = True) 
 
# Remove extra quote the caravan club add to the site address field!
df['SiteAddress'] = df.apply(lambda x: x['SiteAddress'][:-1], axis=1)

# df display 
df 

Longitude   Latitude                           SiteName   PhoneNumber  \
0     -4.252842  51.564412                        Eastmoor CL  01792 390708   
1     -4.276866  51.566973                      Mewslade View  01792 390560   
2     -3.039743  52.949784                        Halton Farm  01691 772401   
3     -3.283912  51.474474                          Greendown  07711 576884   
4     -3.262260  51.440710                      Vishwell Farm  02920 593365   
...         ...        ...                                ...           ...   
2219  -1.652566  52.900279                     Dishfield Farm  01283 732347   
2220   0.711029  51.738064                      Saltcote Hall  01621 853252   
2221  -0.312815  54.218383                Newbiggin East Farm  01723 512189   
2222  -0.944777  52.193677                      Gayton Marina  01604 858685   
2223   0.065016  50.934835  The Laughing Fish Public House CL  01825 750349   

                                            SiteAddress  
0      Kimley Moor Farm, Rhossili, Swansea, Swansea,...  
1      Middleton, Rhossili, Swansea, Swansea, SA3 1P...  
2              Chirk, Wrexham, Wrexham, LL14 5BG, Wales  
3      Drope Road, St. George's-Super-Ely, Cardiff, ...  
4              Wenvoe, Cardiff, Cardiff, CF5 6AF, Wales  
...                                                 ...  
2219   Sutton-on-the-Hill, Ashbourne, Derbyshire, DE...  
2220   Goldhanger Road, Heybridge, Maldon, Essex, CM...  
2221   Scarborough Road, Filey, North Yorkshire, YO1...  
2222   Blisworth Arm, Blisworth, Northampton, Northa...  
2223   Station Road, Isfield, Uckfield, East Sussex,...  

[2224 rows x 5 columns]

In [9]:
# Convert the phone number to a string so we can add it to folium and kml
df['PhoneNumber'] = df['PhoneNumber'].astype(str)
df['PhoneNumber']

0       01792 390708
1       01792 390560
2       01691 772401
3       07711 576884
4       02920 593365
            ...     
2219    01283 732347
2220    01621 853252
2221    01723 512189
2222    01604 858685
2223    01825 750349
Name: PhoneNumber, Length: 2224, dtype: object

### Now create kml file for use by maps.me
### Once the .kml file has been created for maps.me will need to edit the file and change all instances of <styleUrl>#<number></styleUrl> with a valid maps.me styleUrl
    
<styleUrl>#placemark-blue</styleUrl>
<styleUrl>#placemark-red</styleUrl>
<styleUrl>#placemark-green</styleUrl>
<styleUrl>#placemark-yellow</styleUrl>
<styleUrl>#placemark-brown</styleUrl>
<styleUrl>#placemark-orange</styleUrl>
<styleUrl>#placemark-pink</styleUrl>    
<styleUrl>#placemark-purple</styleUrl>

In [10]:
kml = simplekml.Kml()
style = simplekml.Style()
style.iconstyle.icon.href = 'http://maps.google.com/mapfiles/kml/paddle/red-blank.png'
style.iconstyle.scale = 1

map = folium.Map(location=[54.0, -1.0], zoom_start=6)
for index, row in df.iterrows():
    name = row['SiteName']
    address = row['SiteAddress']+ ', ' + row['PhoneNumber']
    phonenumber = row['PhoneNumber']
    coords = [(row['Longitude'], row['Latitude'])]
    pnt = kml.newpoint(name=name)
    pnt.coords = coords
    pnt.style = style
    pnt.phonenumber = phonenumber
    pnt.description = address
    
    popupText = folium.Html('<p>'+row['SiteName']+'</p><p>'+row['SiteAddress']+'</p><p>'+row['PhoneNumber']+'</p>', script=True)
    #popupText = folium.Html('<p>'+row['SiteName']+'</p><p>'+row['SiteAddress']+'</p>', script=True)
    popup = folium.Popup(popupText, max_width=300)
    folium.Marker([row['Latitude'], row['Longitude']],
                 popup=popup,
                 icon=folium.Icon(color='red', icon='info-sign')).add_to(map)
    
kml.save(path="poi/cc-cl-2021.kml")
map.save("poi/cc-cl-2021.html")
map